In [2]:
import pandas as pd
from matplotlib import pyplot as plt
import numpy as np
import pickle
import plotly.express as px
import plotly.graph_objects as go

import dash
from dash import html,Input,Output,dcc
from dash.dependencies import Input, Output, State
import geopandas as gpd


path = '../'

def load_augumented(code):
    file = path + 'data/augumented/' + code + '.pkl'
    with open(file, 'rb') as f:
        df = pickle.load(f)
    return df
countries = ["BG", "GR", "HR", "RO", "RS", "SI"]
country_dict = {
"BG":"Bulgaria",
"GR":"Greece",
"HR":"Croatia",
"RO":"Romania",
"RS":"Republic of Serbia",
"SI":"Slovenia",
}

In [16]:
code = 'RO'
df = load_augumented(code)
df.drop(columns=["Price-1","Price-2","Price-24","Load-1","Load-24"])

DayAheadPrice  GenBiomass  GenFossilBrownCoal  \
2022-01-02 00:00:00+00:00          52.59        57.0               969.0   
2022-01-02 01:00:00+00:00          43.09        58.0               868.0   
2022-01-02 02:00:00+00:00          20.21        58.0               881.0   
2022-01-02 03:00:00+00:00           9.70        58.0               920.0   
2022-01-02 04:00:00+00:00           9.70        58.0               834.0   
...                                  ...         ...                 ...   
2023-02-28 19:00:00+00:00         174.69        47.0              1043.0   
2023-02-28 20:00:00+00:00         159.57        47.0              1006.0   
2023-02-28 21:00:00+00:00         154.68        50.0              1013.0   
2023-02-28 22:00:00+00:00         144.12        50.0              1012.0   
2023-02-28 23:00:00+00:00         135.37        57.0              1021.0   

                           GenFossilGas  GenFossilHardCoal  GenHydroRiver  \
2022-01-02 00:00:00+00:00         843.0               46.0         1378.0   
2022-01-02 01:00:00+00:00         844.0               46.0         1354.0   
2022-01-02 02:00:00+00:00         841.0               46.0         1394.0   
2022-01-02 03:00:00+00:00         838.0               47.0         1358.0   
2022-01-02 04:00:00+00:00         836.0               46.0         1145.0   
...                                 ...                ...            ...   
2023-02-28 19:00:00+00:00        1729.0              167.0         1841.0   
2023-02-28 20:00:00+00:00        1719.0              156.0         1850.0   
2023-02-28 21:00:00+00:00        1501.0              125.0         1854.0   
2023-02-28 22:00:00+00:00        1219.0              125.0         1844.0   
2023-02-28 23:00:00+00:00        1168.0              125.0         1653.0   

                           GenHydroReservoir  GenNuclear  GenSolar  GenWind  \
2022-01-02 00:00:00+00:00              188.0      1422.0       0.0   1052.0   
2022-01-02 01:00:00+00:00              179.0      1422.0       0.0   1324.0   
2022-01-02 02:00:00+00:00              203.0      1421.0       0.0   1385.0   
2022-01-02 03:00:00+00:00              192.0      1422.0       0.0   1522.0   
2022-01-02 04:00:00+00:00              169.0      1422.0       0.0   1904.0   
...                                      ...         ...       ...      ...   
2023-02-28 19:00:00+00:00             1003.0      1396.0       0.0     44.0   
2023-02-28 20:00:00+00:00              998.0      1396.0       0.0     37.0   
2023-02-28 21:00:00+00:00              752.0      1395.0       0.0     40.0   
2023-02-28 22:00:00+00:00              737.0      1395.0       0.0     42.0   
2023-02-28 23:00:00+00:00              629.0      1396.0       0.0     61.0   

                           ...  LoadActual  Temperature  Precipitation  \
2022-01-02 00:00:00+00:00  ...      5055.0          3.8            0.0   
2022-01-02 01:00:00+00:00  ...      4991.0          3.7            0.0   
2022-01-02 02:00:00+00:00  ...      4967.0          3.6            0.0   
2022-01-02 03:00:00+00:00  ...      5014.0          3.3            0.0   
2022-01-02 04:00:00+00:00  ...      5133.0          2.8            0.0   
...                        ...         ...          ...            ...   
2023-02-28 19:00:00+00:00  ...      7385.0          3.9            0.0   
2023-02-28 20:00:00+00:00  ...      6902.0          3.8            0.0   
2023-02-28 21:00:00+00:00  ...      6421.0          3.7            0.0   
2023-02-28 22:00:00+00:00  ...      6004.0          3.6            0.0   
2023-02-28 23:00:00+00:00  ...      5833.0          3.6            0.0   

                           SolarRad  PowerUnavailable  GenTotal  ImportTotal  \
2022-01-02 00:00:00+00:00         0             460.0    5955.0         83.0   
2022-01-02 01:00:00+00:00         0             460.0    6095.0         56.0   
2022-01-02 02:00:00+00:00         0             460.0    6229.0         33.0   
2022-01-02 03:00:00+00:00      

In [4]:
gen_cols = []
imp_cols = []
fossil_cols = []
for col in df.columns:
    if col[:3] == 'Gen' and col[-5:] != "Total":
        gen_cols.append(col)
    if col[:6] == 'Import':
        imp_cols.append(col)
    if col[:9] == 'GenFossil':
        fossil_cols.append(col)
#display(gen_cols)
#for i, y in enumerate(gen_cols):
#    print(i,y)

In [5]:
colors = ['#e6194B', '#3cb44b', '#ffe119', '#4363d8', '#f58231', '#911eb4', '#42d4f4', '#f032e6', '#bfef45', '#fabed4', '#469990', '#dcbeff', '#9A6324', '#fffac8', '#800000', '#aaffc3', '#808000', '#ffd8b1', '#000075', '#a9a9a9', '#000000']
display(df)

DayAheadPrice  GenBiomass  GenFossilBrownCoal  \
2022-01-02 00:00:00+00:00          52.59        57.0               969.0   
2022-01-02 01:00:00+00:00          43.09        58.0               868.0   
2022-01-02 02:00:00+00:00          20.21        58.0               881.0   
2022-01-02 03:00:00+00:00           9.70        58.0               920.0   
2022-01-02 04:00:00+00:00           9.70        58.0               834.0   
...                                  ...         ...                 ...   
2023-02-28 19:00:00+00:00         174.69        47.0              1043.0   
2023-02-28 20:00:00+00:00         159.57        47.0              1006.0   
2023-02-28 21:00:00+00:00         154.68        50.0              1013.0   
2023-02-28 22:00:00+00:00         144.12        50.0              1012.0   
2023-02-28 23:00:00+00:00         135.37        57.0              1021.0   

                           GenFossilGas  GenFossilHardCoal  GenHydroRiver  \
2022-01-02 00:00:00+00:00         843.0               46.0         1378.0   
2022-01-02 01:00:00+00:00         844.0               46.0         1354.0   
2022-01-02 02:00:00+00:00         841.0               46.0         1394.0   
2022-01-02 03:00:00+00:00         838.0               47.0         1358.0   
2022-01-02 04:00:00+00:00         836.0               46.0         1145.0   
...                                 ...                ...            ...   
2023-02-28 19:00:00+00:00        1729.0              167.0         1841.0   
2023-02-28 20:00:00+00:00        1719.0              156.0         1850.0   
2023-02-28 21:00:00+00:00        1501.0              125.0         1854.0   
2023-02-28 22:00:00+00:00        1219.0              125.0         1844.0   
2023-02-28 23:00:00+00:00        1168.0              125.0         1653.0   

                           GenHydroReservoir  GenNuclear  GenSolar  GenWind  \
2022-01-02 00:00:00+00:00              188.0      1422.0       0.0   1052.0   
2022-01-02 01:00:00+00:00              179.0      1422.0       0.0   1324.0   
2022-01-02 02:00:00+00:00              203.0      1421.0       0.0   1385.0   
2022-01-02 03:00:00+00:00              192.0      1422.0       0.0   1522.0   
2022-01-02 04:00:00+00:00              169.0      1422.0       0.0   1904.0   
...                                      ...         ...       ...      ...   
2023-02-28 19:00:00+00:00             1003.0      1396.0       0.0     44.0   
2023-02-28 20:00:00+00:00              998.0      1396.0       0.0     37.0   
2023-02-28 21:00:00+00:00              752.0      1395.0       0.0     40.0   
2023-02-28 22:00:00+00:00              737.0      1395.0       0.0     42.0   
2023-02-28 23:00:00+00:00              629.0      1396.0       0.0     61.0   

                           ...  Price-1  Price-2  Price-24  Load-1  Load-24  \
2022-01-02 00:00:00+00:00  ...    57.08    43.08     41.33  5202.0   5704.0   
2022-01-02 01:00:00+00:00  ...    52.59    57.08     43.09  5055.0   5502.0   
2022-01-02 02:00:00+00:00  ...    43.09    52.59     45.46  4991.0   5349.0   
2022-01-02 03:00:00+00:00  ...    20.21    43.09     37.67  4967.0   5274.0   
2022-01-02 04:00:00+00:00  ...     9.70    20.21     39.70  5014.0   5258.0   
...                        ...      ...      ...       ...     ...      ...   
2023-02-28 19:00:00+00:00  ...   194.18   193.87    174.49  7709.0   7341.0   
2023-02-28 20:00:00+00:00  ...   174.69   194.18    160.30  7385.0   6835.0   
2023-02-28 21:00:00+00:00  ...   159.57   174.69    153.46  6902.0   6324.0   
2023-02-28 22:00:00+00:00  ...   154.68   159.57    149.46  6421.0   6017.0   
2023-02-28 23:00:00+00:00  ...   144.12   154.68    134.00  6004.0   5744.0   

                           GenTotal  ImportTotal  GenFossilTotal  Hour  Month  
2022-01-02 00:00:00+00:00    5955.0         83.0          1858.0     0      1  
2022-01-02 01:00:00+00:00    6095.0         56.0          1758.0     1      1  
2022-01-02 02:00:00+00:00    6229.0         33.0   

In [6]:
def plotGeneration(roll_window=24):
        if roll_window!=0: copy = df.copy().rolling(window=roll_window).mean()
        else: copy = df.copy()

        fig = go.Figure()
        for i,col in enumerate(gen_cols):
                color = colors[i]
                visibility='legendonly'
                visibility=True
                fig.add_trace(go.Scatter(x=copy.index, 
                                        y=copy[col], 
                                        name=col,
                                        mode='lines',
                                        line_width=0,
                                        fillcolor=colors[i],
                                        stackgroup='one',
                                        visible=visibility))
                                        #groupnorm='percent'))
        fig.add_trace(go.Scatter(x=copy.index, 
                                y=copy["GenTotal"], 
                                name="GenTotal",
                                mode="lines",
                                line_color="black"))  
        #fig.add_trace(go.Scatter(x=df.index, y=df["DayAheadPrice"], name='High 2014'))
        #fig.add_trace(go.Scatter(x=df.index, y=df["DayAheadPrice"], name='High 2014'))
        fig.update_layout(
                title={'text':'Rolling Average of Power Generation in %s with window of %.i hours' % (country_dict[code], roll_window),
                       'x':0.5, 
                       'xanchor':'center'},
                yaxis_title='Power Generation (MW)',
                xaxis_title='Date',
                showlegend=True)
        fig.show()
plotGeneration(24)

In [7]:
def plotPrice(roll_window=24):
        roll_copy = df.copy().rolling(window=roll_window).mean()
        copy = df.copy()
        #if roll_window!=0: copy = df.copy().rolling(window=roll_window).mean()
        #else: copy = df.copy()

        fig = go.Figure()
        fig.add_trace(go.Scatter(x=copy.index, 
                                y=copy["DayAheadPrice"], 
                                name="GenTotal",
                                mode="lines",
                                line_color="black"))  
        fig.add_trace(go.Scatter(x=roll_copy.index, 
                                y=roll_copy["DayAheadPrice"], 
                                name="Rolling average %.i h" % (roll_window),
                                mode="lines",
                                line_color="red")) 
        fig.update_layout(
                title={'text':'Raw Data of Energy Prices in %s' % (country_dict[code]),
                       'x':0.5, 'xanchor':'center'},
                yaxis_title='Price (EUR/MWh)',
                xaxis_title='Date',
                showlegend=True)
        fig.show()
plotPrice(24)

In [8]:
from functions import *

In [22]:
def plotPricePrediction(roll_window=24):
        test_size=0.5
        model, params, selected_features, err, predictions = train_model_country('rf', df, 20, test_size=test_size)
        def train(dataframe):
                return dataframe[:int((1-test_size)*dataframe.shape[0])]
        def test(dataframe):
                return dataframe[int((1-test_size)*dataframe.shape[0]):]
        def rolling(dataframe):
                return dataframe.rolling(window=roll_window).mean()
        
        copy = df.copy()
        
        fig = go.Figure()
        fig.add_trace(go.Scatter(x=copy.index, 
                                y=copy["DayAheadPrice"], 
                                name="Train price",
                                mode="lines",
                                line_color="blue"))  
        fig.add_trace(go.Scatter(x=copy).index, 
                                y=rolling(copy)["DayAheadPrice"], 
                                name="Rolling average of train prive",
                                mode="lines",
                                line_color="midnightblue"))
        display(predictions)
        fig.add_trace(go.Scatter(x=predictions.index, 
                                y=predictions,
                                name="Prediction",
                                mode="lines",
                                line_color="orange"))  #
        fig.add_trace(go.Scatter(x=predictions.index, 
                                y=rolling(predictions), 
                                name="Rolling average of prediction",
                                mode="lines",
                                line_color="red"))  
        #fig.add_trace(go.Scatter(x=roll_copy.index, 
        #                        y=roll_copy["DayAheadPrice"], 
        #                        name="Rolling average %.i h" % (roll_window),
        #                        mode="lines",
        #                        line_color="red")) 
        fig.update_layout(
                title={'text':'Prediction of Energy Price in %s' % (country_dict[code]),'x':0.5, 'xanchor':'center'},
                yaxis_title='Price (EUR/MWh)',
                xaxis_title='Date',
                showlegend=True)
        return fig, selected_features, err, params
fig, selected_features, err, params = plotPricePrediction(24)

2022-08-01 09:00:00+00:00    437.937692
2022-08-01 10:00:00+00:00    440.704672
2022-08-01 11:00:00+00:00    399.271851
2022-08-01 12:00:00+00:00    389.776554
2022-08-01 13:00:00+00:00    383.738452
                                ...    
2023-02-28 19:00:00+00:00    195.625136
2023-02-28 20:00:00+00:00    169.146978
2023-02-28 21:00:00+00:00    157.468430
2023-02-28 22:00:00+00:00    159.507703
2023-02-28 23:00:00+00:00    142.363014
Length: 5074, dtype: float64

In [23]:
fig.show()

In [13]:
from dash import Dash, dash_table
import pandas as pd
def generate_table(series):
    frame = pd.DataFrame({'Metric':series.index, 'Value':series.values})
    return frame.to_html()
new = generate_table(err)

<table border="1" class="dataframe">
  <thead>
    <tr style="text-align: right;">
      <th></th>
      <th>Metric</th>
      <th>Value</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <th>0</th>
      <td>Root mean squared error</td>
      <td>58.682354</td>
    </tr>
    <tr>
      <th>1</th>
      <td>Coefficient of variation RMSE</td>
      <td>0.224217</td>
    </tr>
    <tr>
      <th>2</th>
      <td>Normalized mean bias error</td>
      <td>0.027412</td>
    </tr>
    <tr>
      <th>3</th>
      <td>R2 score</td>
      <td>0.873968</td>
    </tr>
  </tbody>
</table>


In [15]:
def generate_table(dataframe, max_rows=10):
    return html.Table([
        #html.Thead(
        #    html.Tr([html.Th(col) for col in dataframe.columns])
        #),
        html.Tbody([
            html.Tr([
                html.Td(dataframe.iloc[i][col]) for col in dataframe.columns
            ]) for i in range(min(len(dataframe), max_rows))
        ])
    ])
frame = pd.DataFrame({'Metric':err.index, 'Value':err.values})
generate_table(frame)

Table([Tbody([Tr([Td('Root mean squared error'), Td(58.682354486395305)]), Tr([Td('Coefficient of variation RMSE'), Td(0.2242171307791625)]), Tr([Td('Normalized mean bias error'), Td(0.02741183078614439)]), Tr([Td('R2 score'), Td(0.8739677858843424)])])])

In [11]:


dff = pd.read_csv('https://raw.githubusercontent.com/plotly/datasets/master/solar.csv')
display(dff)
dash_table.DataTable(dff.to_dict('records'), [{"name": i, "id": i} for i in dff.columns])

State  Number of Solar Plants  Installed Capacity (MW)  \
0      California                     289                     4395   
1         Arizona                      48                     1078   
2          Nevada                      11                      238   
3      New Mexico                      33                      261   
4        Colorado                      20                      118   
5           Texas                      12                      187   
6  North Carolina                     148                      669   
7        New York                      13                       53   

   Average MW Per Plant  Generation (GWh)  
0                  15.3             10826  
1                  22.5              2550  
2                  21.6               557  
3                   7.9               590  
4                   5.9               235  
5                  15.6               354  
6                   4.5              1162  
7                   4.1                84

DataTable(data=[{'State': 'California', 'Number of Solar Plants': 289, 'Installed Capacity (MW)': 4395, 'Average MW Per Plant': 15.3, 'Generation (GWh)': 10826}, {'State': 'Arizona', 'Number of Solar Plants': 48, 'Installed Capacity (MW)': 1078, 'Average MW Per Plant': 22.5, 'Generation (GWh)': 2550}, {'State': 'Nevada', 'Number of Solar Plants': 11, 'Installed Capacity (MW)': 238, 'Average MW Per Plant': 21.6, 'Generation (GWh)': 557}, {'State': 'New Mexico', 'Number of Solar Plants': 33, 'Installed Capacity (MW)': 261, 'Average MW Per Plant': 7.9, 'Generation (GWh)': 590}, {'State': 'Colorado', 'Number of Solar Plants': 20, 'Installed Capacity (MW)': 118, 'Average MW Per Plant': 5.9, 'Generation (GWh)': 235}, {'State': 'Texas', 'Number of Solar Plants': 12, 'Installed Capacity (MW)': 187, 'Average MW Per Plant': 15.6, 'Generation (GWh)': 354}, {'State': 'North Carolina', 'Number of Solar Plants': 148, 'Installed Capacity (MW)': 669, 'Average MW Per Plant': 4.5, 'Generation (GWh)': 11

In [12]:
def generate_table(dataframe, max_rows=10):
    return html.Table([
        #html.Thead(
        #    html.Tr([html.Th(col) for col in dataframe.columns])
        #),
        html.Tbody([
            html.Tr([
                html.Td(dataframe.iloc[i][col]) for col in dataframe.columns
            ]) for i in range(min(len(dataframe), max_rows))
        ])
    ])
generate_table(err)

AttributeError: 'Series' object has no attribute 'columns'

In [ ]:
df.head()

DayAheadPrice  GenBiomass  GenFossilBrownCoal  \
2022-01-02 00:00:00+00:00          52.59         7.0               206.0   
2022-01-02 01:00:00+00:00          48.97         7.0               208.0   
2022-01-02 02:00:00+00:00          34.94         7.0               207.0   
2022-01-02 03:00:00+00:00          29.56         7.0               200.0   
2022-01-02 04:00:00+00:00          33.97         7.0               207.0   

                           GenFossilGas  GenFossilOil  GenHydroPumped  \
2022-01-02 00:00:00+00:00          55.0           0.0             0.0   
2022-01-02 01:00:00+00:00          54.0           0.0             0.0   
2022-01-02 02:00:00+00:00          54.0           0.0             0.0   
2022-01-02 03:00:00+00:00          56.0           0.0             0.0   
2022-01-02 04:00:00+00:00          58.0           0.0             0.0   

                           GenHydroRiver  GenNuclear  GenSolar  GenWaste  ...  \
2022-01-02 00:00:00+00:00          107.0       693.0       0.0      11.0  ...   
2022-01-02 01:00:00+00:00          107.0       693.0       0.0      11.0  ...   
2022-01-02 02:00:00+00:00          107.0       693.0       0.0      11.0  ...   
2022-01-02 03:00:00+00:00          106.0       693.0       0.0      11.0  ...   
2022-01-02 04:00:00+00:00          105.0       693.0       0.0      11.0  ...   

                           Price-1  Price-2  Price-24  Load-1  Load-24  \
2022-01-02 00:00:00+00:00    57.08    85.16     51.44  1077.0   1127.0   
2022-01-02 01:00:00+00:00    52.59    57.08     55.91  1036.0   1083.0   
2022-01-02 02:00:00+00:00    48.97    52.59     46.94  1019.0   1053.0   
2022-01-02 03:00:00+00:00    34.94    48.97     37.67  1012.0   1047.0   
2022-01-02 04:00:00+00:00    29.56    34.94     39.70  1013.0   1066.0   

                           GenTotal  ImportTotal  GenFossilTotal  Hour  Month  
2022-01-02 00:00:00+00:00    1079.0       1874.0           261.0     0      1  
2022-01-02 01:00:00+00:00    1080.0       1474.0           262.0     1      1  
2022-01-02 02:00:00+00:00    1079.0        847.0           261.0     2      1  
2022-01-02 03:00:00+00:00    1073.0       1151.0           256.0     3      1  
2022-01-02 04:00:00+00:00    1081.0       1668.0           265.0     4      1  

[5 rows x 29 columns]

In [ ]:
N = len(countries)
geoplot_columns = ["DayAheadPrice",'LoadActual']
n = len(geoplot_columns)
values = {"ISO":countries}
for i in range(n):
    values[geoplot_columns[i]]=np.zeros(N)
    
for i,code in enumerate(countries):
    df = load_augumented(code)
    copy = df.copy()
    for j,column in enumerate(geoplot_columns):
        values[column][i] = copy[column].mean()

indicators = pd.DataFrame.from_dict(values,orient='index').transpose()
indicators[geoplot_columns] = indicators[geoplot_columns].astype(float)
merged = gpd.GeoDataFrame(geo.merge(indicators, on='ISO', how='left'))

In [ ]:
value1 = 'LoadActual'
value2 = "DayAheadPrice"
def update_map(column):
    # Filter data by selection
    filtered_df = merged[[column, 'geometry', 'COUNTRY']]
    display(filtered_df)
    # Create the choropleth map
    fig = px.choropleth(
        filtered_df, 
        geojson=filtered_df.geometry, 
        locations=filtered_df.index, 
        scope="europe",
        color=column, 
        color_continuous_scale='reds', 
        #range_color=(240, 270), 
        projection='natural earth',
        #labels={'Energy Consumption':'Energy Consumption (kWh)'}
    )

    fig.update_geos(
        center=dict(lon=21, lat=43), 
        lataxis_range=[30, 45], 
        lonaxis_range=[9, 30]
    )    
    
    fig.update_layout(coloraxis_showscale=True,
                      margin={"r":0,"t":0,"l":0,"b":0})
    
    return fig
update_map(value1)

LoadActual                                           geometry   COUNTRY
0  4427.112414  POLYGON ((22.93560 41.34213, 22.95590 41.35562...  Bulgaria
1  2080.919228  MULTIPOLYGON (((17.57853 42.94383, 17.51889 42...   Croatia
2  5567.410229  MULTIPOLYGON (((21.08305 39.05666, 21.04527 39...    Greece
3  6440.189218  POLYGON ((24.31971 43.69664, 24.30778 43.69749...   Romania
4  3819.879559  POLYGON ((20.07142 42.56091, 20.09993 42.65770...    Serbia
5  1543.710161  POLYGON ((15.30709 45.62986, 15.29400 45.59454...  Slovenia